In [ ]:
# !python3.10.10 -m pip install numpy
# !python3.10 -m pip install pyparsing
# !python3.10 -m pip install -U matplotlib
# !python3.10 -m pip install  pandas
!python3.10 -m pip install  datapackage
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from os import listdir
from os.path import isfile, join
from pipeline_utils import *
import pickle
import re
import datapackage
import random
from datetime import datetime, timedelta
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)


data_path = '../local_path' # change data path accordingly
resource_path = './resources' # change resource path accordingly

### Load in static_data.csv and convert all features to the right datatype
Argument:

    data_path -- path of mimic data directory 
    resource_path -- resource directory of mimic-pipeline-tools/mimic-iv-v2-0 repo

Return:

    data_df -- dataframe of static info

In [2]:
static_df = load_static_df(data_path, resource_path)
print(len(static_df))
static_df.head(10)

76943


subject_id   hadm_id gender                    race        age  \
stay_id                                                                    
39553978    10000032  29079034      F                   WHITE  52.559969   
39765666    10000980  26913865      F  BLACK/AFRICAN AMERICAN  76.486231   
37067082    10001217  24597018      F                   WHITE  55.881486   
34592300    10001217  27703517      F                   WHITE  55.962942   
31205490    10001725  25563031      F                   WHITE  46.275517   
37510196    10001884  26184834      F  BLACK/AFRICAN AMERICAN  77.018296   
39060235    10002013  23581541      F                   OTHER  57.378803   
32358465    10002155  20345487      F                   WHITE  83.186535   
33685454    10002155  23822395      F                   WHITE  81.592179   
31090461    10002155  28994087      F                   WHITE  82.729467   

         insurance           admittime           dischtime  \
stay_id                                                      
39553978  Medicaid 2180-07-23 12:35:00 2180-07-25 17:55:00   
39765666  Medicare 2189-06-27 07:38:00 2189-07-03 03:00:00   
37067082     Other 2157-11-18 22:56:00 2157-11-25 18:00:00   
34592300     Other 2157-12-18 16:58:00 2157-12-24 14:55:00   
31205490     Other 2110-04-11 15:08:00 2110-04-14 15:00:00   
37510196  Medicare 2131-01-07 20:39:00 2131-01-20 05:15:00   
39060235  Medicare 2160-05-18 07:45:00 2160-05-23 13:30:00   
32358465     Other 2131-03-09 20:33:00 2131-03-10 01:55:00   
33685454     Other 2129-08-04 12:44:00 2129-08-18 16:53:00   
31090461     Other 2130-09-23 21:59:00 2130-09-29 18:55:00   

                    discharge_location  fullcode_first  dnr_first  fullcode  \
stay_id                                                                       
39553978                          HOME             1.0        0.0       1.0   
39765666              HOME HEALTH CARE             1.0        0.0       1.0   
37067082              HOME HEALTH CARE             NaN        NaN       NaN   
34592300              HOME HEALTH CARE             1.0        0.0       1.0   
31205490                          HOME             1.0        0.0       1.0   
37510196                          DIED             NaN        NaN       NaN   
39060235              HOME HEALTH CARE             1.0        0.0       1.0   
32358465                          DIED             NaN        NaN       NaN   
33685454  CHRONIC/LONG TERM ACUTE CARE             NaN        NaN       NaN   
31090461              HOME HEALTH CARE             1.0        0.0       1.0   

          dnr dnr_first_charttime timecmo_chart  cmo_first  cmo_last  cmo  \
stay_id                                                                     
39553978  0.0                 NaT           NaT        0.0       0.0  0.0   
39765666  0.0                 NaT           NaT        0.0       0.0  0.0   
37067082  NaN                 NaT           NaT        NaN       NaN  NaN   
34592300  0.0                 NaT           NaT        0.0       0.0  0.0   
31205490  0.0                 NaT           NaT        0.0       0.0  0.0   
37510196  NaN                 NaT           NaT        NaN       NaN  NaN   
39060235  0.0                 NaT           NaT        0.0       0.0  0.0   
32358465  NaN                 NaT           NaT        NaN       NaN  NaN   
33685454  NaN                 NaT           NaT        NaN       NaN  NaN   
31090461  0.0                 NaT           NaT        0.0       0.0  0.0   

                   deathtime          icu_intime         icu_outtime  los_icu  \
stay_id                                                                         
39553978                 NaT 2180-07-23 14:00:00 2180-07-23 23:50:47     0.41   
39765666                 NaT 2189-06-27 08:42:00 2189-06-27 20:38:27     0.50   
37067082                 NaT 2157-11-20 19:18:02 2157-11-21 22:08:00     1.12   
34592300                 NaT 2157-12-19 15:42:24 2157-12-20 14:27:41     

In [3]:
static_df.columns

Index(['subject_id', 'hadm_id', 'gender', 'race', 'age', 'insurance',
       'admittime', 'dischtime', 'discharge_location', 'fullcode_first',
       'dnr_first', 'fullcode', 'dnr', 'dnr_first_charttime', 'timecmo_chart',
       'cmo_first', 'cmo_last', 'cmo', 'deathtime', 'icu_intime',
       'icu_outtime', 'los_icu', 'admission_type', 'first_careunit',
       'mort_icu', 'mort_hosp', 'hospital_expire_flag', 'hospstay_seq',
       'icustay_seq', 'readmission_30'],
      dtype='object')

### regroup ethnicity; redefine the regrouping or skip if not desirable
Argument:

    df -- static dataframe
    d -- regroup dictionary {original race: new race}

Return:

    df -- dataframe of static info with race regrouped


In [4]:
d = {'WHITE.*':'white','ASIAN.*':'asian','BLACK.*':'black','AMERICAN INDIAN.*':'amer indian',\
      'CARIBBEAN ISLAND':'other','HISPANIC.*':'hisp/latino','MULTI RACE ETHNICITY':'other',\
     'PATIENT DECLINED TO ANSWER':'other','PORTUGUESE':'south amer/port','SOUTH AMERICAN':'south amer/port',\
      'UNABLE TO OBTAIN':'other','UNKNOWN.*':'other','.*PACIFIC ISLANDER':'other','OTHER':'other','AMERICAN':'other'}
static_df = regroup_ethnicity(static_df, d=d)
print ('race categories after regrouping',np.unique(static_df.race_regroup,return_counts=True))

race categories after regrouping (array(['amer indian', 'asian', 'black', 'hisp/latino',
       'multiple race/ethnicity', 'other', 'south amer/port', 'white'],
      dtype=object), array([  152,  2265,  8358,  2894,    74, 10711,   399, 52090]))


In [5]:
df_crystalloid_bolus.head()

NameError: name 'df_crystalloid_bolus' is not defined

In [6]:

df_Norepinephrine = pd.read_csv("../local_path/treatments/norepinephrine.csv")
df_Vasopressin =  pd.read_csv("../local_path/treatments/vasopressin.csv")
df_Phenylephrine =  pd.read_csv("../local_path/treatments/phenylephrine.csv")
df_Dopamine =  pd.read_csv("../local_path/treatments/dopamine.csv")
df_Epinephrine =  pd.read_csv("../local_path/treatments/epinephrine.csv")

# preprocess each of these files

print(df_Vasopressin)


        stay_id  linkorderid    vaso_rate  vaso_amount            starttime  \
0      32128372      6396958     1.200000     1.940000  2137-02-26 00:05:00   
1      32128372      6396958     2.401264    37.979998  2137-02-26 01:42:00   
2      32128372      1644957     2.402402    39.999998  2137-02-26 17:31:00   
3      32128372      5824862     2.401262     5.963134  2137-02-27 10:10:00   
4      38383343      9527519     2.439024    39.999999  2137-08-19 00:14:00   
5      38383343      7200533     2.400000    39.879999  2137-08-19 16:38:00   
6      38383343       361942     2.400000    38.720003  2137-08-20 09:15:00   
7      38383343      6757312     2.400000    39.920003  2137-08-21 01:23:00   
8      38383343      2396102     2.400000    40.679999  2137-08-21 18:01:00   
9      38383343      4643798     2.402402    39.999998  2137-08-22 10:58:00   
10     38383343       266487     2.400000    39.879999  2137-08-23 03:37:00   
11     38383343      5308934     2.400000    39.9599

In [7]:
# fluid administration events
#   filter for  NaCl 0.9% or  lactated ringers or blood transfusions (packed red blood cells, fresh frozen plasma, or platelets)
#   Further filtering for: fluid administrations with a volume of at least 250mL and for a period of 60 minutes or shorter
df_crystalloid_bolus = pd.read_csv("../local_path/treatments/crystalloid_bolus.csv")
df_colloid_bolus = pd.read_csv("../local_path/treatments/colloid_bolus.csv")



In [8]:
df_colloid_bolus.head(5)

# df_colloid_bolus['charttime'] = pd.to_datetime(df_colloid_bolus['charttime'])

# Sort the DataFrame by 'charttime'
df_colloid_bolus = df_colloid_bolus.sort_values('charttime')
df_colloid_bolus.head(5)

stay_id            charttime  colloid_bolus
1650   30588857  2110-01-11 20:45:00            500
1651   30588857  2110-01-12 11:50:00            250
18606  36817845  2110-01-13 20:45:00            500
18607  36817845  2110-01-13 21:57:00            500
18608  36817845  2110-01-14 02:20:00            500

In [9]:
df_crystalloid_bolus.head(5)
df_crystalloid_bolus = df_crystalloid_bolus.sort_values('charttime')
df_crystalloid_bolus.head(5)


stay_id            charttime  crystalloid_bolus
10106  30588857  2110-01-11 13:00:00                500
10107  30588857  2110-01-11 14:15:00                500
10108  30588857  2110-01-11 15:53:00                500
10109  30588857  2110-01-11 17:16:00                500
10110  30588857  2110-01-12 01:50:00                500

In [10]:
from datetime import datetime, timedelta
def compare_timestamps(time1, time2):
    format = "%Y-%m-%d %H:%M:%S"
    datetime1 = datetime.strptime(time1, format)
    datetime2 = datetime.strptime(time2, format)
    if datetime1 < datetime2:
        return -1
    elif datetime1 > datetime2:
        return 1
    else:
        return 0

# def add_to_df(df, time, id, bolus_value):
#     if id in df.columns:
#         if not df[id].empty:
#             df.at[df.index[-1], id].append((time, bolus_value))
#         else:
#             df.at[df.index[-1], id] = [(time, bolus_value)]
#     else:
#         df[id] = [[(time, bolus_value)]]
#     return df
# def add_to_df(df, time, id, bolus_value):
#     # Create a tuple for the new entry
#     new_entry = (time, bolus_value)
    
#     # Check if the column (ID) already exists
#     if id in df.columns:
#         # Append the new entry to the existing list in the column
#         df.loc[0, id].append(new_entry)
#     else:
#         # If ID does not exist, create a new column with a new list
#         df[id] = [[new_entry]]

#     return df

def add_to_df(df, time, id, bolus_value):
    # Create a tuple for the new entry
    new_entry = (time, bolus_value)
    
    # Check if the row (ID) already exists in the DataFrame's index
    if id in df.index:
        # Append the new entry to the existing list in the row
        df.at[id, 'Data'].append(new_entry)
    else:
        # If ID does not exist, create a new row with this ID and a new list
        df.loc[id] = [[new_entry]]

    return df

In [11]:
from datetime import datetime, timedelta
import pandas as pd

df_bolus = pd.DataFrame(columns=['Data'])
df_bolus.index.name = 'stay_id'
# used to compare the timestamp format
# returns -1 if 1 < 2 and +1 if 1 > 2

colloid_i = 0
crystalloid_i = 0
while colloid_i < len(df_colloid_bolus) and crystalloid_i < len(df_crystalloid_bolus):
    colloid_bolus_stay_id = df_colloid_bolus.iloc[colloid_i]['stay_id']
    colloid_bolus_charttime = df_colloid_bolus.iloc[colloid_i]['charttime']
    colloid_bolus_colloid_bolus = df_colloid_bolus.iloc[colloid_i]['colloid_bolus']
    
    crystalloid_bolus_stay_id = df_crystalloid_bolus.iloc[colloid_i]['stay_id']
    crystalloid_bolus_charttime = df_crystalloid_bolus.iloc[colloid_i]['charttime']
    crystalloid_bolus_colloid_bolus = df_crystalloid_bolus.iloc[colloid_i]['crystalloid_bolus']
    
    # returns -1 if 1 < 2, +1 if 1 > 2, and 0 if equal
    timestamp_compare_val = compare_timestamps(colloid_bolus_charttime, crystalloid_bolus_charttime) == -1
    if timestamp_compare_val == -1:
        colloid_i +=1
        df_bolus = add_to_df(df_bolus, colloid_bolus_charttime, colloid_bolus_stay_id, colloid_bolus_colloid_bolus)
    elif timestamp_compare_val == 1:
        crystalloid_i +=1
        df_bolus = add_to_df(df_bolus, crystalloid_bolus_charttime, crystalloid_bolus_stay_id, crystalloid_bolus_colloid_bolus)
    elif timestamp_compare_val == 0:
        crystalloid_i+=1
        colloid_i +=1
        
        df_bolus = add_to_df(df_bolus, crystalloid_bolus_charttime, crystalloid_bolus_stay_id, str(int(colloid_bolus_colloid_bolus) + int(crystalloid_bolus_colloid_bolus)))
        

In [12]:
# count = 0
# for col in df_bolus.columns:
#     col_list = df_bolus[col][0]
#     for tuple in range(0, len(col_list)):
        
#         val = col_list[tuple][1]
#         if int(val) < 250:
#             count+=1
# print(count)

df_bolus.head(5)

Data
stay_id                                                    
30588857  [(2110-01-11 13:00:00, 1000), (2110-01-11 14:1...
38319097                      [(2110-01-12 11:02:00, 1000)]
36817845  [(2110-01-13 12:40:00, 800), (2110-01-13 16:01...
38339174                       [(2110-01-18 11:30:00, 830)]
34901199  [(2110-01-19 03:45:00, 1500), (2110-01-19 12:0...

In [36]:
from datetime import datetime


def compare_timestamps(time1, time2):
    # Define the date format
    format = "%Y-%m-%d %H:%M:%S"
    
    # Convert string to datetime objects
    datetime1 = datetime.strptime(time1, format)
    datetime2 = datetime.strptime(time2, format)
    
    # Compare the two datetime objects
    if datetime1 < datetime2:
        return -1
    elif datetime1 > datetime2:
        return 1
    else:
        return 0

# Example usage
result = compare_timestamps("2174-09-29 22:00:00", "2174-09-29 22:00:00")
print("Comparison Result:", result)

Comparison Result: 0


In [ ]:

icuids = labs_df['stay_id'].unique()
treatments = ['norepinephrine', 'vasopressin', 'phenylephrine', 'dopamine', 'epinephrine']
vaso_treatments = load_treatments(data_path, icuids, treatments)

# select the vassopressin vaso_rate that are less than or equal to 0.2
vaso_treatments['vasopressin'] = vaso_treatments['vasopressin'][vaso_treatments['vasopressin']['vaso_rate'] <= 0.2]

# multiply the vaso_rate of vasopressin by 5
vaso_treatments['vasopressin']['vaso_rate'] = vaso_treatments['vasopressin']['vaso_rate']*5

# multiply the vaso_rate of phenylephrine by 0.45
vaso_treatments['phenylephrine']['vaso_rate'] = vaso_treatments['phenylephrine']['vaso_rate']*0.45

# multiply the vaso_rate of dopamine by 0.01
vaso_treatments['dopamine']['vaso_rate'] = vaso_treatments['dopamine']['vaso_rate']*0.01


### Plot histogram 
A quick overview of demographic info

In [ ]:
def plot_hist_static(df):
    fig, axs = plt.subplots(7,3,figsize=(15,48))
    i = 0
    for f in df.columns[2:]:
        title_f = f
#         if f == 'discharge_location': continue
        if df[f].dtype.name=='datetime64[ns]': continue
        elif f=='los_icu':
            axs[i//3][i%3].hist(df[f],weights=w, bins = 50)
            title_f = 'los_icu(in days)'
        elif df[f].dtype.name=='category' or df[f].dtype.name=='object':
            w = np.ones(len(df))/len(df)*100
            if f=='race':
                continue
            elif f in ['race_regroup','admission_type','first_careunit']:
                axs[i//3][i%3].hist(df[f].str.lower(),weights=w)
                axs[i//3][i%3].tick_params(axis='x',labelrotation=-45)
            elif f=='discharge_location':
                axs[i//3][i%3].hist(df.discharge_location.fillna('nan').str.lower(),weights=w)
                axs[i//3][i%3].tick_params(axis='x',labelrotation=-45)


            else:
                axs[i//3][i%3].hist(df[f],weights=w)
                    
        else:
            axs[i//3][i%3].hist(df[f].dropna(),weights=np.ones(len(df[f].dropna()))/len(df[f])*100)
        axs[i//3][i%3].set_title('{}: {:.2f}% missing data'.format(title_f,100.-len(df[f].dropna())/len(df[f])*100))
        axs[i//3][i%3].set_ylim([0.,100.])
        axs[i//3][i%3].set_ylabel('%')
        
        i+=1
    plt.show()
plot_hist_static(static_df)

### Select patient cohort based on following args
Argument:
 
    df -- static dataframe to be filtered
    min_age -- minimal age (default 18; youngest patient in cohort is 18;)
    max_age -- maximal age (default 90; ages of patients older than 90 may have been shifted)
    min_duration -- minimum length of stay (hr) in icu (default 12 hrs)
    max_duration -- maximum length of stay (hr) in icu (default 240 hrs, varies from hours to months)
    hosq_seq -- <= i-th time of vising hospital (ranges from 1-30, default none and select all)
    icustay_seq -- <= i-th time of admission icu (ranges from 1-7, default none and select all)
    mort_hosp -- hospital mortality (0-survival to hospital discharge, 1-death in hosp, default none and select all)
    mort_icu -- icu mortality (0-survival to icu discharge, 1-death in icu, default none and select all)
    readmission_30 -- readmission in 30 days (0-no readmission, 1-readmission to icu, default none and select all)

Output:

    df -- filtered static dataframe

    



In [ ]:
selected_static_df = select_patient_cohort(static_df, min_age = 18, max_age = 90, min_duration = 24, max_duration = None,
                                           hosq_seq = None, icustay_seq = None, mort_hosp = None,
                                           mort_icu = None, readmission_30 = None)

selected_patients = selected_static_df[selected_static_df['icustay_seq'] != 1]['subject_id'].unique()
selected_static_df = selected_static_df[selected_static_df['subject_id'].isin(selected_patients)]
selected_static_df = selected_static_df[selected_static_df['icustay_seq'] == 1]
print(len(selected_static_df))

In [ ]:
# mean arterial 
variable_range_df = get_variable_ranges(resource_path)
union_df, impute_tb = aggr_dynamic_features(['mean_blood_pressure(arterial)'], selected_static_df.index, data_path, variable_range_df, exlusion='valid', lq=0.05,hq=0.95, imputation_stats='mean')
union_df = union_df[union_df['mean_blood_pressure'] <= 65]
union_df = union_df.groupby(['stay_id'])['mean_blood_pressure'].count() >= 7 

In [ ]:
len(union_df)

In [ ]:
df_crystalloid_bolus = pd.read_csv("local_path/treatments/crystalloid_bolus.csv")
df_colloid_bolus = pd.read_csv("../../local_path/treatments/co_bolus.csv")

### aggregate demographic info, comorbidity scores and sepsis label
Argument:

    data_path -- str: path of data folder
    df -- dataframe: static info dataframe
    demo_features -- list of strs: demographic features one want to select (default None and select all)
    comorbidity -- list of strs: comorbidity scores one want to select (default None; options: columns in comorbidity/charlson.csv)
    include_sepsis -- bool: if include sepsis-III label (default False)

Return:

    df -- dataframe aggregating demographic info, comorbidity scores and sepsis label

In [17]:
# specifiy static features which include demographic, sepsis definition, commorbidity score, first day measurements

# valid option: every column inside static_data.csv 
demo_features = ['age','gender','race_regroup','insurance','los_icu']

# valid option: 'charlson' and other scores used to caculate cci (columns charlson.csv)
comorbidity = ['charlson_comorbidity_index','dementia','congestive_heart_failure']
# if include sepsis label
include_sepsis = True

selected_static_df = aggr_static(data_path, selected_static_df,demo_features=demo_features,\
                                 comorbidity=comorbidity,include_sepsis=include_sepsis)
selected_static_df.head()

Reading charlson comorbidity score: ['charlson_comorbidity_index', 'dementia', 'congestive_heart_failure']
Finished concat comorbidity scores... 
Finished concat sepsis labels... 


age gender race_regroup insurance  los_icu  subject_id  \
stay_id                                                                  
34617352  52.867878      M        other  Medicaid     1.75    10006053   
38229329  67.513409      M        white     Other     1.15    10026255   
38210605  59.628389      M        white     Other     1.03    10030579   
33536886  72.648885      M        white  Medicare     1.16    10034317   
39005188  80.099100      M        other  Medicare     1.91    10048105   

           hadm_id          icu_intime         icu_outtime  \
stay_id                                                      
34617352  22942076 2111-11-14 00:19:12 2111-11-15 18:21:10   
38229329  22059910 2201-07-10 10:10:47 2201-07-11 13:48:02   
38210605  27018952 2183-08-19 09:33:41 2183-08-20 10:23:36   
33536886  20827960 2159-08-30 12:35:14 2159-08-31 16:26:27   
39005188  28885740 2159-02-08 15:50:19 2159-02-10 13:33:46   

          charlson_comorbidity_index  dementia  congestive_heart_failure  \
stay_id                                                                    
34617352                           6         0                         0   
38229329                          11         0                         0   
38210605                           4         0                         0   
33536886                           9         0                         0   
39005188                          12         0                         0   

          sepsis3  
stay_id            
34617352      1.0  
38229329      0.0  
38210605      0.0  
33536886      0.0  
39005188      0.0

### Load in variable range table
Note: for now, we are using the same resource file as that in MIMIC-III; modify (add more variables in the future) if needed; 

Argument: 

    resource_path -- path of resource folder
Return:

    var_range -- table of variable ranges



In [18]:
variable_range_df = get_variable_ranges(resource_path)
display(variable_range_df)

OUTLIER_LOW  VALID_LOW  IMPUTE  \
VARIABLE                                                             
alanine_aminotransferase                    0.0       2.00   34.00   
albumin                                     0.0       0.60    3.10   
alkaline_phosphate                          0.0      20.00  106.00   
anion_gap                                   0.0       5.00   13.00   
asparate_aminotransferase                   0.0       6.00   40.00   
bicarbonate                                 0.0       0.00   25.00   
bilirubin                                   0.0       0.10    0.90   
blood_urea_nitrogen                         0.0       0.00   23.00   
capillary_refill_rate                       0.0       0.00    0.00   
chloride                                    0.0      50.00  104.00   
cholesterol                                 0.0      32.00  160.00   
creatinine                                  0.0       0.10    1.00   
diastolic_blood_pressure                    0.0       0.00   59.00   
fraction_inspired_oxygen                    0.2       0.21    0.21   
gcs                                         3.0       3.00   11.00   
glucose                                     0.0      33.00  128.00   
heart_rate                                  0.0       0.00   86.00   
height                                      0.0       0.00  170.00   
hematocrit                                  0.0       0.00   30.20   
hemoglobin                                  0.0       0.00   10.20   
lactate                                     0.0       0.40    1.80   
lactate_dehydrogenase                       0.0      54.00  263.00   
magnesium                                   0.0       0.00    2.00   
mean_blood_pressure                         0.0      14.00   77.00   
oxygen_saturation                           0.0       0.00   98.00   
partial_pressure_of_carbon_dioxide          0.0       0.00   40.00   
partial_pressure_of_oxygen                  0.0      32.00  112.00   
partial_thromboplastin_time                 0.0      18.80   34.40   
peak_inspiratory_pressure                   0.0      14.00   20.00   
ph                                          6.3       6.30    7.40   
phosphate                                   0.0       0.50    3.40   
platelets                                   0.0       0.00  208.00   
positive_end-expiratory_pressure            0.0       0.00    6.00   
potassium                                   0.0       0.00    4.10   
prothrombin_time_inr                        0.0       0.90    1.30   
prothrombin_time_pt                         0.0       9.90   14.50   
respiratory_rate                            0.0       0.00   19.00   
sodium                                      0.0      50.00  142.00   
systolic_blood_pressure                     0.0       0.00  118.00   
temperature                                14.2      26.00   37.00   
troponin-i                                  0.0       0.01    2.30   
troponin-t                                  0.0       0.01    0.10   
urine_output                                0.0       0.00   80.00   
weight                                      0.0       0.00   81.80   
white_blood_cell_count                      0.0       0.00    9.90   

                                    VALID_HIGH  OUTLIER_HIGH  
VARIABLE                                                      
alanine_aminotransferase              10000.00       11000.0  
albumin                                   6.00          60.0  
alkaline_phosphate                     3625.00        4000.0  
anion_gap                                50.00          55.0  
asparate_aminotransferase             20000.00       22000.0  
bicarbonate                              60.00          66.0  
bilirubin                                60.00          66.0  
blood_urea_nitrogen                     250.00         275.0  
capillary_refill_rate                     1.00           1.0  
chloride                                175.00      

### Specify static features, dynamic features, treatment to be included

In [19]:
icuids = list(selected_static_df.index)


In [20]:
vitals_and_labs = [

            'creatinine',
            'fraction_inspired_oxygen',
            'lactate',
            'urine_output',
            'alanine_aminotransferase',
            'asparate_aminotransferase',
            'diastolic_blood_pressure',
            'systolic_blood_pressure',
            'mean_blood_pressure',
            'partial_pressure_of_oxygen',
            'gcs'
            
            ]           

### Aggregate all dynamic features
Arguments

    features -- dynamic feature list; if level 1 desired, speicify it with (level1) with no bracket between (e.g. mean_blood_pressure(arterial)); all files in vitals_and_labs/ are valid options
    icuids -- icuids from selected patient cohort
    variable_ranges -- variable range/impute value table
    data_path -- data path
    exclusion ---- ways to exclue outliers (not all variables have ranges specified)
              ---- default none: include all
              ---- outlier: exclude extreme(nearly impossible) feature valuenums
              ---- valid: exclude rare (but possible) feature valuenums
              (Note: not all variables have a range specified in the table
               if not specified, we use quantile (lq/hq) as exclusion criterion)
    lq -- exlude data lower than low quantile value (default 0)
    hq -- exlude data lower than low quantile value (default 1)
    imputation_stats ---- statistics to store in the imputation table (default mean)
                     ---- mean
                     ---- median



 Return
 
    union_df -- unioned dynamic feature table with ['stay_id','charttime'] as index (table contains lots of nans, which we will fix it later)
    impute_tb -- imputation value table (if not in table, use mean)



In [22]:
union_df,impute_tb = aggr_dynamic_features(vitals_and_labs,icuids, data_path,variable_range_df, exlusion='outlier',lq=0.0,hq=1.,imputation_stats='mean' )

Using mean as imputation stats
finish reading creatinine.csv
Dropping values that are 999999.0
	 0.0% data excluded
finish reading fraction_inspired_oxygen.csv
Dropping values that are 999999.0
	 0.013576894593927413% data excluded
finish reading lactate.csv
Dropping values that are 999999.0
	 0.0% data excluded
finish reading urine_output.csv
Dropping values that are 999999.0
	 0.0006265433236281037% data excluded
finish reading alanine_aminotransferase.csv
Dropping values that are 999999.0
	 0.0% data excluded
finish reading asparate_aminotransferase.csv
Dropping values that are 999999.0
	 0.0008368200836820217% data excluded
finish reading diastolic_blood_pressure.csv
Dropping values that are 999999.0
	 3.446077502278211e-05% data excluded
finish reading systolic_blood_pressure.csv
Dropping values that are 999999.0
	 1.7226825612892682e-05% data excluded
finish reading mean_blood_pressure.csv
Dropping values that are 999999.0
	 0.0003093315002578034% data excluded
finish reading par

In [24]:
impute_tb

{'creatinine': 1.0,
 'fraction_inspired_oxygen': 0.21,
 'lactate': 1.8,
 'urine_output': 80.0,
 'alanine_aminotransferase': 34.0,
 'asparate_aminotransferase': 40.0,
 'diastolic_blood_pressure': 59.0,
 'systolic_blood_pressure': 118.0,
 'mean_blood_pressure': 77.0,
 'partial_pressure_of_oxygen': 112.0,
 'gcs': 11.0}

#### Update patient id list

In [25]:
union_df = union_df.groupby('stay_id').filter(lambda x: x['mean_blood_pressure'].notnull().sum() >= 7 and (x['mean_blood_pressure'] <= 65).sum() >= 7)

union_df.head(5)

creatinine  fraction_inspired_oxygen  lactate  \
stay_id  charttime                                                            
30007765 2154-01-23 02:10:00         2.0                       NaN      NaN   
         2154-01-23 04:18:00         NaN                       NaN      NaN   
         2154-01-23 04:30:00         NaN                       NaN      NaN   
         2154-01-23 04:42:00         NaN                       NaN      NaN   
         2154-01-23 04:45:00         NaN                       NaN      NaN   

                              urine_output  alanine_aminotransferase  \
stay_id  charttime                                                     
30007765 2154-01-23 02:10:00           NaN                       NaN   
         2154-01-23 04:18:00           NaN                       NaN   
         2154-01-23 04:30:00           NaN                       NaN   
         2154-01-23 04:42:00           NaN                       NaN   
         2154-01-23 04:45:00           NaN                       NaN   

                              asparate_aminotransferase  \
stay_id  charttime                                        
30007765 2154-01-23 02:10:00                        NaN   
         2154-01-23 04:18:00                        NaN   
         2154-01-23 04:30:00                        NaN   
         2154-01-23 04:42:00                        NaN   
         2154-01-23 04:45:00                        NaN   

                              diastolic_blood_pressure  \
stay_id  charttime                                       
30007765 2154-01-23 02:10:00                       NaN   
         2154-01-23 04:18:00                      52.0   
         2154-01-23 04:30:00                      54.0   
         2154-01-23 04:42:00                       NaN   
         2154-01-23 04:45:00                      53.0   

                              systolic_blood_pressure  mean_blood_pressure  \
stay_id  charttime                                                           
30007765 2154-01-23 02:10:00                      NaN                  NaN   
         2154-01-23 04:18:00                    123.0                 68.0   
         2154-01-23 04:30:00                     92.0                 63.0   
         2154-01-23 04:42:00                      NaN                  NaN   
         2154-01-23 04:45:00                     91.0                 61.0   

                              partial_pressure_of_oxygen   gcs  
stay_id  charttime                                              
30007765 2154-01-23 02:10:00                         NaN   NaN  
         2154-01-23 04:18:00                         NaN   NaN  
         2154-01-23 04:30:00                         NaN   NaN  
         2154-01-23 04:42:00                         NaN  15.0  
         2154-01-23 04:45:00                         NaN   NaN

In [26]:
icuids = list((set(union_df.index.get_level_values(0))))
icuids
union_df.index.get_level_values(0)

Int64Index([30007765, 30007765, 30007765, 30007765, 30007765, 30007765,
            30007765, 30007765, 30007765, 30007765,
            ...
            39990748, 39990748, 39990748, 39990748, 39990748, 39990748,
            39990748, 39990748, 39990748, 39990748],
           dtype='int64', name='stay_id', length=36610)

#### Help function to load treatments and exclude extreme values
Arguments

    data_path -- path of data folder
    icuids -- list of icuids to be included
    treatments -- list of treatments names; all files in treatments/ are valid options

Return

    tr_df -- dictionary with treatment names as keys and treatment dataframes as values


In [27]:
treatments = [

    'colloid_bolus', # -- fluid
    'crystalloid_bolus', #-- fluid
    'norepinephrine',  # --vaso
    'vasopressin',  # --vaso
    'phenylephrine',  # --vaso
    'dopamine', # --vaso
    'epinephrine',  # --vaso

    ]

In [28]:
tr_df = load_treatments(data_path, icuids, treatments)
tr_df

finish reading colloid_bolus.csv
finish reading crystalloid_bolus.csv
finish reading norepinephrine.csv
finish reading vasopressin.csv
finish reading phenylephrine.csv
finish reading dopamine.csv
finish reading epinephrine.csv


{'colloid_bolus':           amount           starttime
 stay_id                             
 30110791     250 2151-02-06 04:32:00
 30185043     250 2185-02-08 22:30:00
 30336685     500 2112-10-31 23:00:00
 30370537     250 2175-05-03 18:11:00
 30775445     500 2146-05-10 02:00:00
 30807243     500 2112-10-10 20:10:00
 30807243     500 2112-10-10 22:43:00
 30836761     250 2205-01-26 21:14:00
 30836761     500 2205-01-27 00:58:00
 30910612     500 2180-11-09 20:31:00
 30910612     500 2180-11-10 01:43:00
 30912037     250 2181-06-07 19:51:00
 30912037     250 2181-06-08 00:00:00
 31496550     500 2143-01-30 14:18:00
 31496550     500 2143-01-30 15:18:00
 31791269     500 2163-03-07 20:53:00
 31844244     250 2161-01-13 14:28:00
 31844244     250 2161-01-13 18:28:00
 31922886     500 2132-12-04 22:30:00
 31926647     500 2125-11-26 22:00:00
 31941316     500 2118-10-01 17:50:00
 31941316     500 2118-10-01 18:30:00
 32030984     500 2198-11-24 12:16:00
 32149161     250 2140-08-22 15:2

#### Aggregate vitals and labs with static features (if any) and treatments (if any); 

Arguments
 
    dyn_df -- big union table of all vitals and labs from previous step
    impute_tb -- Table of imputation values
    static_df -- static info dataframe (default none)
    tr_df -- treatment dataframe dictionary from previous step (default {})
    traj_cut -- if cut trajectory to certain length (default 100,000, which is large enough to keep all)
    t_w -- feature binning time window length in hour (default 1)
    start_ts -- starting timestamp (if admit, using icu admission time; if treatment, use timestamp of first treatment; default treatment)
    binning -- how to bin treatment (irregular versus regular; default: irregular)
    norm_treatment -- if normalizing and aggregate treatment dosage, including vaso and fluid 
                           (default true; note not all vasos are implemented)
    fill_na -- if filling nans (if true use forward filling; if there are still nans, use impute table )





In [30]:
aggr_df = feature_aggr(union_df, \
                       impute_tb, \
                       icuids, \
                       start_ts='admit',\
                       static_df=selected_static_df,\
                       t_w=1.,binning='irregular',tr_df = tr_df,fill_na = True,norm_treatment=True)
aggr_df.head(50)

Finish process # 499 patients
normalizing colloid_bolus ...
normalizing crystalloid_bolus ...
normalizing norepinephrine ...
normalizing vasopressin ...
normalizing phenylephrine ...
normalizing dopamine ...
normalizing epinephrine ...


creatinine  \
stay_id  time                                                     
37453824 [2177-11-16 08:01:01, 2177-11-16 09:01:01)         1.2   
         [2177-11-16 09:01:01, 2177-11-16 10:01:01)         1.2   
         [2177-11-16 10:01:01, 2177-11-16 11:01:01)         1.2   
         [2177-11-16 11:01:01, 2177-11-16 12:01:01)         1.2   
         [2177-11-16 12:01:01, 2177-11-16 13:01:01)         1.2   
         [2177-11-16 13:01:01, 2177-11-16 14:01:01)         1.2   
         [2177-11-16 14:01:01, 2177-11-16 15:01:01)         1.2   
         [2177-11-16 15:01:01, 2177-11-16 16:01:01)         1.2   
         [2177-11-16 16:01:01, 2177-11-16 17:01:01)         1.2   
         [2177-11-16 17:01:01, 2177-11-16 18:01:01)         1.2   
         [2177-11-16 18:01:01, 2177-11-16 19:01:01)         1.2   
         [2177-11-16 19:01:01, 2177-11-16 20:01:01)         1.2   
         [2177-11-16 20:01:01, 2177-11-16 21:01:01)         1.2   
         [2177-11-16 21:01:01, 2177-11-16 22:01:01)         1.2   
         [2177-11-16 22:01:01, 2177-11-16 23:01:01)         1.2   
         [2177-11-16 23:01:01, 2177-11-17 00:01:01)         1.2   
         [2177-11-17 00:01:01, 2177-11-17 01:01:01)         1.2   
         [2177-11-17 01:01:01, 2177-11-17 02:01:01)         1.2   
         [2177-11-17 02:01:01, 2177-11-17 03:01:01)         1.2   
         [2177-11-17 03:01:01, 2177-11-17 04:01:01)         1.2   
         [2177-11-17 04:01:01, 2177-11-17 05:01:01)         1.2   
         [2177-11-17 05:01:01, 2177-11-17 06:01:01)         1.2   
         [2177-11-17 06:01:01, 2177-11-17 07:01:01)         1.2   
         [2177-11-17 07:01:01, 2177-11-17 08:01:01)         1.2   
         [2177-11-17 08:01:01, 2177-11-17 09:01:01)         1.2   
         [2177-11-17 09:01:01, 2177-11-17 10:01:01)         1.2   
         [2177-11-17 10:01:01, 2177-11-17 11:01:01)         1.2   
         [2177-11-17 11:01:01, 2177-11-17 12:01:01)         1.2   
         [2177-11-17 12:01:01, 2177-11-17 13:01:01)         1.2   
         [2177-11-17 13:01:01, 2177-11-17 14:01:01)         1.2   
         [2177-11-17 14:01:01, 2177-11-17 15:01:01)         1.2   
         [2177-11-17 15:01:01, 2177-11-17 16:01:01)         1.2   
         [2177-11-17 16:01:01, 2177-11-17 17:01:01)         1.2   
         [2177-11-17 17:01:01, 2177-11-17 18:01:01)         1.2   
         [2177-11-17 18:01:01, 2177-11-17 19:01:01)         1.2   
         [2177-11-17 19:01:01, 2177-11-17 20:01:01)         1.2   
         [2177-11-17 20:01:01, 2177-11-17 21:01:01)         1.2   
         [2177-11-17 21:01:01, 2177-11-17 22:01:01)         1.2   
38436866 [2166-11-18 08:47:27, 2166-11-18 09:47:27)         1.0   
         [2166-11-18 09:47:27, 2166-11-18 10:47:27)         1.0   
         [2166-11-18 10:47:27, 2166-11-18 11:47:27)         1.0   
         [2166-11-18 11:47:27, 2166-11-18 12:47:27)         1.0   
         [2166-11-18 12:47:27, 2166-11-18 13:47:27)         0.7   
         [2166-11-18 13:47:27, 2166-11-18 14:47:27)         0.7   
         [2166-11-18 14:47:27, 2166-11-18 15:47:27)         0.7   
         [2166-11-18 15:47:27, 2166-11-18 16:47:27)         0.7   
         [2166-11-18 16:47:27, 2166-11-18 17:47:27)         0.7   
         [2166-11-18 17:47:27, 2166-11-18 18:47:27)         0.7   
         [2166-11-18 18:47:27, 2166-11-18 19:47:27)         0.7   
         [2166-11-18 19:47:27, 2166-11-18 20:47:27)         0.7   

                                                     fraction_inspired_oxygen  \
stay_id  time                                                                   
37453824 [2177-11-16 08:01:01, 2177-11-16 09:01:01)                      0.21   
         [2177-11-16 09:01:01, 2177-11-16 10:01:01)                      0.21   
         [2177-11-16 10:01:01, 2177-11-16 11:01:01)                      0.21   
         [2177-11-16 11:01:01, 2177-11-16 12:01:01)                      0.21   
         [2177-11-16 12:01:01, 2177-11-16 13:01:01)                      0.21   
 

In [31]:
aggr_df[aggr_df['crystalloid_bolus(amount)']  >0 ].head()

creatinine  \
stay_id  time                                                     
37453824 [2177-11-16 19:01:01, 2177-11-16 20:01:01)         1.2   
38436866 [2166-11-18 12:47:27, 2166-11-18 13:47:27)         0.7   
31369221 [2122-02-25 02:05:43, 2122-02-25 03:05:43)         1.0   
         [2122-02-25 04:05:43, 2122-02-25 05:05:43)         1.1   
         [2122-02-25 09:05:43, 2122-02-25 10:05:43)         1.1   

                                                     fraction_inspired_oxygen  \
stay_id  time                                                                   
37453824 [2177-11-16 19:01:01, 2177-11-16 20:01:01)                      0.21   
38436866 [2166-11-18 12:47:27, 2166-11-18 13:47:27)                      1.00   
31369221 [2122-02-25 02:05:43, 2122-02-25 03:05:43)                      0.21   
         [2122-02-25 04:05:43, 2122-02-25 05:05:43)                      0.21   
         [2122-02-25 09:05:43, 2122-02-25 10:05:43)                      0.21   

                                                     lactate  urine_output  \
stay_id  time                                                                
37453824 [2177-11-16 19:01:01, 2177-11-16 20:01:01)     1.80         250.0   
38436866 [2166-11-18 12:47:27, 2166-11-18 13:47:27)     1.95          95.0   
31369221 [2122-02-25 02:05:43, 2122-02-25 03:05:43)     1.80         300.0   
         [2122-02-25 04:05:43, 2122-02-25 05:05:43)     1.80          10.0   
         [2122-02-25 09:05:43, 2122-02-25 10:05:43)     0.80         105.0   

                                                     alanine_aminotransferase  \
stay_id  time                                                                   
37453824 [2177-11-16 19:01:01, 2177-11-16 20:01:01)                      34.0   
38436866 [2166-11-18 12:47:27, 2166-11-18 13:47:27)                      34.0   
31369221 [2122-02-25 02:05:43, 2122-02-25 03:05:43)                      34.0   
         [2122-02-25 04:05:43, 2122-02-25 05:05:43)                      11.0   
         [2122-02-25 09:05:43, 2122-02-25 10:05:43)                      11.0   

                                                     asparate_aminotransferase  \
stay_id  time                                                                    
37453824 [2177-11-16 19:01:01, 2177-11-16 20:01:01)                       40.0   
38436866 [2166-11-18 12:47:27, 2166-11-18 13:47:27)                       40.0   
31369221 [2122-02-25 02:05:43, 2122-02-25 03:05:43)                       40.0   
         [2122-02-25 04:05:43, 2122-02-25 05:05:43)                       15.0   
         [2122-02-25 09:05:43, 2122-02-25 10:05:43)                       15.0   

                                                     diastolic_blood_pressure  \
stay_id  time                                                                   
37453824 [2177-11-16 19:01:01, 2177-11-16 20:01:01)                      51.0   
38436866 [2166-11-18 12:47:27, 2166-11-18 13:47:27)                      51.0   
31369221 [2122-02-25 02:05:43, 2122-02-25 03:05:43)                      51.0   
         [2122-02-25 04:05:43, 2122-02-25 05:05:43)                      63.0   
         [2122-02-25 09:05:43, 2122-02-25 10:05:43)                      49.0   

                                                     systolic_blood_pressure  \
stay_id  time                                                                  
37453824 [2177-11-16 19:01:01, 2177-11-16 20:01:01)               101.000000   
38436866 [2166-11-18 12:47:27, 2166-11-18 13:47:27)               109.666667   
31369221 [2122-02-25 02:05:43, 2122-02-25 03:05:43)                81.000000   
         [2122-02-25 04:05:43, 2122-02-25 05:05:43)                98.000000   
         [2122-02-25 09:05:43, 2122-02-25 10:05:43)                94.000000   

                                                     mean_blood_pressure  \
stay_id  time                                                              
37453824 [2177-11-16 19:01:01, 2177-11-16 20

In [32]:
len(aggr_df)

22840

In [33]:
data = aggr_df.copy()

In [34]:
# Initialize an empty dictionary to store the results
result_dict = {}

# Group the DataFrame by the first level of the index
grouped = data.groupby(level='stay_id')

# Iterate through the groups
for first_index, group in grouped:
    # Convert the group to a list of dictionaries (one per row)
    rows = group.to_dict(orient='records')
    # Store the list of features under the first index
    result_dict[first_index] = rows

# Convert the result dictionary to a list
result_list = list(result_dict.values())

# Print the result
print(len(result_list[:1][0]))


37


In [35]:
result_list[0]

[{'creatinine': 1.0,
  'fraction_inspired_oxygen': 0.21,
  'lactate': 1.8,
  'urine_output': 80.0,
  'alanine_aminotransferase': 34.0,
  'asparate_aminotransferase': 40.0,
  'diastolic_blood_pressure': 51.0,
  'systolic_blood_pressure': 96.0,
  'mean_blood_pressure': 61.5,
  'partial_pressure_of_oxygen': 112.0,
  'gcs': 15.0,
  'colloid_bolus(binary)': 0.0,
  'colloid_bolus(amount)': 0.0,
  'crystalloid_bolus(binary)': 0.0,
  'crystalloid_bolus(amount)': 0.0,
  'norepinephrine(binary)': 0.0,
  'norepinephrine(amount)': 0.0,
  'vasopressin(binary)': 0.0,
  'vasopressin(amount)': 0.0,
  'phenylephrine(binary)': 0.0,
  'phenylephrine(amount)': 0.0,
  'dopamine(binary)': 0.0,
  'dopamine(amount)': 0.0,
  'epinephrine(binary)': 0.0,
  'epinephrine(amount)': 0.0,
  'vaso(binary)': 0.0,
  'vaso(amount)': 0.0,
  'bolus(binary)': 0.0,
  'bolus(amount)': 0.0,
  'age': 62.99357830637708,
  'gender': 'F',
  'race_regroup': 'black',
  'insurance': 'Medicare',
  'los_icu': 1.51,
  'charlson_comorbid

In [36]:
list(result_list[0][0].values())

[1.0,
 0.21,
 1.8,
 80.0,
 34.0,
 40.0,
 51.0,
 96.0,
 61.5,
 112.0,
 15.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 62.99357830637708,
 'F',
 'black',
 'Medicare',
 1.51,
 7,
 0,
 0,
 0.0]

In [37]:
data_list = []


for dic in result_list[0]:
    for _ in dic.values():
        print(_)
        
    break
    
    
    

1.0
0.21
1.8
80.0
34.0
40.0
51.0
96.0
61.5
112.0
15.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
62.99357830637708
F
black
Medicare
1.51
7
0
0
0.0


In [39]:
data_list = []

# for _ in range(len(result_list)):
    

In [40]:
result_list[:10]

[[{'creatinine': 1.0,
   'fraction_inspired_oxygen': 0.21,
   'lactate': 1.8,
   'urine_output': 80.0,
   'alanine_aminotransferase': 34.0,
   'asparate_aminotransferase': 40.0,
   'diastolic_blood_pressure': 51.0,
   'systolic_blood_pressure': 96.0,
   'mean_blood_pressure': 61.5,
   'partial_pressure_of_oxygen': 112.0,
   'gcs': 15.0,
   'colloid_bolus(binary)': 0.0,
   'colloid_bolus(amount)': 0.0,
   'crystalloid_bolus(binary)': 0.0,
   'crystalloid_bolus(amount)': 0.0,
   'norepinephrine(binary)': 0.0,
   'norepinephrine(amount)': 0.0,
   'vasopressin(binary)': 0.0,
   'vasopressin(amount)': 0.0,
   'phenylephrine(binary)': 0.0,
   'phenylephrine(amount)': 0.0,
   'dopamine(binary)': 0.0,
   'dopamine(amount)': 0.0,
   'epinephrine(binary)': 0.0,
   'epinephrine(amount)': 0.0,
   'vaso(binary)': 0.0,
   'vaso(amount)': 0.0,
   'bolus(binary)': 0.0,
   'bolus(amount)': 0.0,
   'age': 62.99357830637708,
   'gender': 'F',
   'race_regroup': 'black',
   'insurance': 'Medicare',
   'lo

#### Save dataframe

In [ ]:
# saving_dir = 'curated_data/'
# if not os.path.exists(saving_dir):
#     os.makedirs(saving_dir)
# aggr_df.to_csv(os.path.join(saving_dir,'demonstration.csv'),sep=',')

In [41]:
impute_tb = pd.DataFrame.from_dict(impute_tb.items()).rename(columns={0:'feature',1:'impute_value'}).set_index('feature')
impute_tb.to_csv(os.path.join('','impute_table.csv'),sep=',')

In [42]:
impute_tb

impute_value
feature                                 
creatinine                          1.00
fraction_inspired_oxygen            0.21
lactate                             1.80
urine_output                       80.00
alanine_aminotransferase           34.00
asparate_aminotransferase          40.00
diastolic_blood_pressure           59.00
systolic_blood_pressure           118.00
mean_blood_pressure                77.00
partial_pressure_of_oxygen        112.00
gcs                                11.00

# Jiayu HW

In [43]:
#loading the data
static_df = load_static_df(data_path, resource_path)
variable_range_df = get_variable_ranges(resource_path)





#Filtering age and multiple ICU stays

variable_range_df = get_variable_ranges(resource_path)



jiyau_df = select_patient_cohort(static_df, min_age = 18, max_age = 90, min_duration = 24,max_duration = None,\
                                 hosq_seq = None, icustay_seq=1,\
                                 mort_hosp=0, mort_icu=0, readmission_30=0)

# jiyau_df = jiyau_df[jiyau_df['icustay_seq'] != 1]




In [44]:
jiyau_df.head(5)

subject_id   hadm_id gender   race        age insurance  \
stay_id                                                             
37067082    10001217  24597018      F  WHITE  55.881486     Other   
31205490    10001725  25563031      F  WHITE  46.275517     Other   
39060235    10002013  23581541      F  OTHER  57.378803  Medicare   
33685454    10002155  23822395      F  WHITE  81.592179     Other   
31090461    10002155  28994087      F  WHITE  82.729467     Other   

                   admittime           dischtime  \
stay_id                                            
37067082 2157-11-18 22:56:00 2157-11-25 18:00:00   
31205490 2110-04-11 15:08:00 2110-04-14 15:00:00   
39060235 2160-05-18 07:45:00 2160-05-23 13:30:00   
33685454 2129-08-04 12:44:00 2129-08-18 16:53:00   
31090461 2130-09-23 21:59:00 2130-09-29 18:55:00   

                    discharge_location  fullcode_first  dnr_first  fullcode  \
stay_id                                                                       
37067082              HOME HEALTH CARE             NaN        NaN       NaN   
31205490                          HOME             1.0        0.0       1.0   
39060235              HOME HEALTH CARE             1.0        0.0       1.0   
33685454  CHRONIC/LONG TERM ACUTE CARE             NaN        NaN       NaN   
31090461              HOME HEALTH CARE             1.0        0.0       1.0   

          dnr dnr_first_charttime timecmo_chart  cmo_first  cmo_last  cmo  \
stay_id                                                                     
37067082  NaN                 NaT           NaT        NaN       NaN  NaN   
31205490  0.0                 NaT           NaT        0.0       0.0  0.0   
39060235  0.0                 NaT           NaT        0.0       0.0  0.0   
33685454  NaN                 NaT           NaT        NaN       NaN  NaN   
31090461  0.0                 NaT           NaT        0.0       0.0  0.0   

         deathtime          icu_intime         icu_outtime  los_icu  \
stay_id                                                               
37067082       NaT 2157-11-20 19:18:02 2157-11-21 22:08:00     1.12   
31205490       NaT 2110-04-11 15:52:22 2110-04-12 23:59:56     1.34   
39060235       NaT 2160-05-18 10:00:53 2160-05-19 17:33:33     1.31   
33685454       NaT 2129-08-04 12:45:00 2129-08-10 17:02:38     6.18   
31090461       NaT 2130-09-24 00:50:00 2130-09-27 22:13:41     3.89   

                       admission_type  \
stay_id                                 
37067082                     EW EMER.   
31205490                     EW EMER.   
39060235  SURGICAL SAME DAY ADMISSION   
33685454                     EW EMER.   
31090461                     EW EMER.   

                                            first_careunit  mort_icu  \
stay_id                                                                
37067082               Surgical Intensive Care Unit (SICU)         0   
31205490  Medical/Surgical Intensive Care Unit (MICU/SICU)         0   
39060235      Cardiac Vascular Intensive Care Unit (CVICU)         0   
33685454                          Coronary Care Unit (CCU)         0   
31090461  Medical/Surgical Intensive Care Unit (MICU/SICU)         0   

          mort_hosp  hospital_expire_flag  hospstay_seq  icustay_seq  \
stay_id                                                                
37067082          0                     0             1            1   
31205490          0                     0             1            1   
39060235          0                     0             1            1   
33685454          0                     0             1            1   
31090461          0                     0             2            1   

          readmission_30  
stay_id                   
37067082               0  
31205490               0  
39060235               0  
33685454               0  
31090461               0

In [45]:
#Filtering ICU stays for more than 24 hours


jiyau_df = jiyau_df[jiyau_df['dischtime'] - jiyau_df['admittime']  >= pd.Timedelta(hours=24, minutes=0, seconds=0)]

jiyau_subset = jiyau_df.copy()

In [46]:
# Filtering 7 or more mean arterial pressure (MAP) values of 65mmHg or less

union_df,impute_tb = aggr_dynamic_features(['mean_blood_pressure(arterial)'], jiyau_df.index , data_path,variable_range_df, exlusion='valid',lq=0.05,hq=0.95,imputation_stats='mean' )
jiyau_df = union_df[union_df['mean_blood_pressure'] < 65]
filt = jiyau_df.groupby(['stay_id'])['mean_blood_pressure'].count() >=7 
jiyau_df = jiyau_df[filt[jiyau_df.index.get_level_values('stay_id')].values]

Using mean as imputation stats
finish reading mean_blood_pressure.csv
Dropping values that are 999999.0
selected level 1: mean blood pressure (arterial)
	 0.651787116362628% data excluded


In [ ]:
jiyau_df.head(20)

mean_blood_pressure
stay_id  charttime                               
30003598 2189-04-15 01:10:00                 59.0
         2189-04-15 09:00:00                 63.0
         2189-04-15 10:00:00                 63.0
         2189-04-15 11:00:00                 59.0
         2189-04-15 20:00:00                 64.0
         2189-04-15 20:30:00                 59.0
         2189-04-15 22:00:00                 58.0
         2189-04-16 07:00:00                 64.0
         2189-04-16 09:35:00                 54.0
         2189-04-16 09:40:00                 63.0
         2189-04-16 11:00:00                 64.0
         2189-04-16 12:45:00                 63.0
         2189-04-16 20:00:00                 61.0
         2189-04-16 21:00:00                 58.0
         2189-04-16 23:00:00                 64.0
         2189-04-17 00:00:00                 62.0
         2189-04-17 02:00:00                 61.0
         2189-04-17 03:00:00                 59.0
30004144 2126-04-05 00:00:00                 57.0
         2126-04-05 00:15:00                 58.0

In [ ]:
# only using information captured during the inital 48 hours after admission

def f7(seq):
    seen = set()
    seen_add = seen.add
    return [x for x in seq if not (x in seen or seen_add(x))]

In [ ]:
jiyau_df = jiyau_df.reset_index(level = 'charttime')

In [ ]:
jiyau_df['charttime'] = pd.to_datetime(jiyau_df['charttime'])

In [ ]:
jiyau_df.head(50)

In [ ]:
tuples = []
data = []

for i, stay_id in enumerate(f7(jiyau_df.index)):
#     print('\nstayid:', stay_id)
    for i, time in enumerate(jiyau_df.loc[stay_id]['charttime']):
#         print(time, jiyau_df.loc[stay_id]['mean_blood_pressure'].iloc[i])
        if i ==0:
            start = time
        if (time - start) > timedelta(hours=48):
            break
            
        tuples.append((stay_id, time))
        data.append(jiyau_df.loc[stay_id]['mean_blood_pressure'].iloc[i])

In [ ]:
index = pd.MultiIndex.from_tuples(tuples)
jiyau_df = pd.DataFrame(data = data, index = index, columns= ['mean_blood_pressure'])
jiyau_df.index.set_names(['stay_id', 'charttime'], inplace= True)

In [ ]:
jiyau_df.head(20)

In [ ]:
icuids = list((jiyau_df.index.get_level_values(0)))


# tr_df = load_treatments(data_path,icuids, treatments)


jiyau_df = feature_aggr(union_df, \
                       impute_tb, \
                       icuids, \
                       start_ts='admit',\
                       static_df= jiyau_subset,\
                       t_w=1.,binning='irregular',tr_df = {},fill_na = True,norm_treatment=True)
jiyau_df.head(50)